In [2]:
from pyspark.sql import SparkSession

# Create a DataFrame using SparkSession
spark = (SparkSession
    .builder
    .appName("data_cleaning")
    .enableHiveSupport()
    .getOrCreate())

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
Exception in thread "main" java.nio.file.NoSuchFileException: /tmp/tmp_2avxdiw/connection18006879467588853077.info
	at java.base/sun.nio.fs.UnixException.translateToIOException(UnixException.java:92)
	at java.base/sun.nio.fs.UnixException.rethrowAsIOException(UnixException.java:111)
	at java.base/sun.nio.fs.UnixException.rethrowAsIOException(UnixException.java:116)
	at java.base/sun.nio.fs.UnixFileSystemProvider.newByteChannel(UnixFileSystemProvider.java:219)
	at java.base/java.nio.file.Files.newByteChannel(Files.java:371)
	at java.base/java.nio.file.Files.createFile(Files.java:648)
	at java.base/java.nio.file.TempFileHelper.create(TempFileHelper.java:137)
	at java.base/java.nio.file.TempFileHelper.createTempFile(TempFileHelper.java:160)
	at java.base/java.nio.file.Files.createTempFile(Files.java:868)
	at org.apache.spark.api.python.PythonGatewayServer$.main

23/01/31 20:02:24 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
# Sorry i seriouly don't know why i have to do this
import pandas as pd

# Read one file
pandas_df = pd.read_json('/home/jazzdung/E-Commerce-Support-System/mr_clean/product.ndjson', lines=True)
df = spark.createDataFrame(pandas_df) 

# # File location and type
# file_location = "/home/jazzdung/Projects/E-Commerce-Support-System/mr_clean/product.ndjson"
# file_type = "json"

# # CSV options
# infer_schema = "false"
# first_row_is_header = "true"
# delimiter = ","

# # The applied options are for CSV files. For other file types, these will be ignored.
# df = spark.read.format(file_type) \
#   .option("inferSchema", infer_schema) \
#     .option("mode", "failFast")\
#     .option("multiline", "true")\
#     .load(file_location)
# #   .option("header", first_row_is_header) \
# #   .option("sep", delimiter) \
# #   .load(file_location)

df.show(1000, truncate=False)

/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:474: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


+------------------------------------------------------------------------------------------------------------------------------------------+---------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

**Chú ý: với các data dạng string, cần bỏ các kí tự đặc biệt (chỉ dữ lại chữ + số)**

**Tên sp**
- Dùng regex để lọc và bỏ những cái string có thể leak giá ra ngoài)
- Lowercase + bỏ kí tự đặc biệt

In [4]:
from pyspark.sql.functions import udf
import pyspark.sql.functions as f
import re

# Lowercase
def lower_case(s):
    return s.lower()

# Remove Yeu thich, Yeu thich+
def remove_liked_product(s):
    s = re.sub('yêu thích\n', '', s)
    s = re.sub('yêu thích\+\n', '', s)
    return s

# Remove contents inside [], option indicate promotion, prices    
def remove_between_square_brackets(s):
    s = re.sub(r'\[.*?\]', '', s)
    return s

# Remove special character
def remove_special_character(s):
    s = re.sub('[^a-z0-9A-Z_àáãạảăắằẳẵặâấầẩẫậèéẹẻẽêềếểễệđìíĩỉịòóõọỏôốồổỗộơớờởỡợùúũụủưứừửữựỳỵỷỹýÀÁÃẠẢĂẮẰẲẴẶÂẤẦẨẪẬÈÉẸẺẼÊỀẾỂỄỆĐÌÍĨỈỊÒÓÕỌỎÔỐỒỔỖỘƠỚỜỞỠỢÙÚŨỤỦƯỨỪỬỮỰỲỴỶỸÝ]+', ' ', s)
    # s = re.sub('[^A-Za-z0-9 ]+', ' ', s)
    s = re.sub(' +', ' ', s)
    return s

# Remove vietnamese character
def no_accent_vietnamese(s):
    # s = re.sub(r'[àáạảãâầấậẩẫăằắặẳẵ]', 'a', s)
    # s = re.sub(r'[èéẹẻẽêềếệểễ]', 'e', s)
    # s = re.sub(r'[òóọỏõôồốộổỗơờớợởỡ]', 'o', s)
    # s = re.sub(r'[ìíịỉĩ]', 'i', s)
    # s = re.sub(r'[ùúụủũưừứựửữ]', 'u', s)
    # s = re.sub(r'[ỳýỵỷỹ]', 'y', s)
    # s = re.sub(r'[đ]', 'd', s)
    return s

# Remove redundant spaces
def remove_spaces(s):
    s = s.lstrip()
    return s

# Bundled up
def clean_product_name(name):
    name = lower_case(name)
    name = remove_liked_product(name)
    name = remove_between_square_brackets(name)
    name = no_accent_vietnamese(name)
    name = remove_special_character(name)
    name = remove_spaces(name)

    return name

udf_clean_product_name = udf(clean_product_name)

# df.withColumn("product_name", udf_clean_product_name(df["product_name"])).select("product_name").show(10, truncate=False)


**Giá sp**
- Bỏ chữ “đ" (đ55.000)

In [5]:
# 50.000đ -> 50.000
def remove_dong(s):
    s = re.sub('₫', '', s)
    return s

# 50.000 -> 50000
def remove_dot(s):
    s = re.sub('\.', '', s)
    return s

# ₫48.000 - ₫59.000 -> ₫48.000
def remove_second_price (s):
    s = s.split('-')[0]
    s = re.sub(' ', '', s)
    return s

def clean_price(s):
    if s != '':
        s = remove_dong(s)
        s = remove_dot(s)
        s = remove_second_price(s)
        return s
    else:
        return 0

udf_clean_price = udf(clean_price)

# df.withColumn("new_price", udf_clean_price(df["price"])).select("new_price").show(10, truncate=False)

**Chi tiết sp (dạng String)**
- Phải bỏ html
- Dùng regex để lọc và bỏ những cái string có thể leak giá ra ngoài)
- Lowercase + bỏ kí tự đặc biệt

In [6]:
# Make the description somehow readable

def clean_desc(s):

    # chắp vá với các category có "-"
    s = re.sub('Vớ/ Tất', 'Vớ, Tất', s)
    s = re.sub('Quần Dài-Quần Âu', 'Quần Dài, Quần Âu', s)    

    # deal with "&"
    s = re.sub(' &amp;', ',', s)

    # remove links, icon, divider
    s = re.sub('<svg.*?</svg>', '', s)
    s = re.sub('<div>', '', s)   
    s = re.sub('div', '', s)

    # Group lables into 1 row
    s = re.sub('</a>', '-', s)  

    # I don't even remember how this work
    s = re.sub('</label>', ': ', s)
    s = re.sub('class=', '', s)
    s = re.sub('"', '', s)
    s = re.sub('< ', '<', s)    
    s = re.sub("\/.*?\>","/>", s)

    # Delete redundant texts, spaces
    s = re.sub('<label.*?>', '', s)
    s = re.sub('<flex.*?>', '', s)
    s = re.sub(' href=/', '', s)
    s = re.sub('<a ', '<', s)
    s = re.sub('<p ', '<', s)
    s = re.sub(' +', ' ', s)

    # s = re.sub('</svg>', '', s)
    # s = re.sub('</path>', '', s)
    # s = re.sub('<svg.*?>', '', s)
    # s = re.sub('<path.*?>', '', s)

    #Split
    s = re.sub('</>', '/', s)
    s = re.sub('<.*?>', '', s)
    s = s.split("/")
    s = [x for x in s if x!= '']

    return s

udf_clean_desc = udf(clean_desc)

# df.withColumn("new_product_desc", udf_clean_desc(df["product_desc"])).select("new_product_desc").show(1000, truncate=False)

**Product's country**

In [7]:
# Get country
def get_country(s):
    desc_list = clean_desc(s)
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]
    country = ""
    for x in desc_list:
        if "Xuất xứ" in x:
            country = re.sub('.*?: ', '', x)
            country = lower_case(country)
            country = no_accent_vietnamese(country)
            country = remove_special_character(country)


    return country
udf_get_country = udf(get_country)

**Product's brand**

In [8]:
# Get brand
def get_brand(s):
    desc_list = clean_desc(s)
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]
    brand = ""
    for x in desc_list:
            if "Thương hiệu" in x:
                brand = re.sub('.*?: ', '', x)
                brand = lower_case(brand)
                brand = no_accent_vietnamese(brand)
                brand = remove_special_character(brand)

    return brand[:-1]

udf_get_brand= udf(get_brand)

**Product stock**

In [9]:
# Get stock
def get_stock(s):
    desc_list = clean_desc(s)

    # Remove everything after 'MÔ TẢ SẢN PHẨM'
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]

    value = ""
    for x in desc_list:
        if "Kho hàng" in x:
            value = re.sub('.*?: ', '', x)
    
    return value

udf_get_stock= udf(get_stock)


**Product Origin**

In [10]:
# Get origin
def get_origin(s):
    desc_list = clean_desc(s)

    # Remove everything after 'MÔ TẢ SẢN PHẨM'
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]

    value = ""
    for x in desc_list:
        if "Gửi từ" in x:
            value = re.sub('.*?: ', '', x)
            value = lower_case(value)
            value = no_accent_vietnamese(value)
            value = remove_special_character(value)

    
    return value

udf_get_origin= udf(get_origin)

**Description (MÔ TẢ SẢN PHẨM)**

In [11]:
# Get description inside of description, god forbid these naming
def get_smaller_desc_list(s):
    desc_list = clean_desc(s)

    # GET everything after 'MÔ TẢ SẢN PHẨM'
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[truncate_index+1:]

    value = ' '.join(desc_list)
    value = lower_case(value)
    value = no_accent_vietnamese(value)   
    value = remove_special_character(value)

    return value

    # if len(desc_list) == 1:
    #     desc_list = ''.join(desc_list)
    #     return desc_list 
    # else:
    #     desc_list = ' \n '.join(desc_list)
    #     return desc_list 

udf_get_smaller_desc_list = udf(get_smaller_desc_list)

**Category**    
- Phân category ra làm 3 tầng, sẽ có 3 attribute là cat1,cat2, cat3
- cat2 có format là :”cat1 / cat2”, cat3 là “cat1 / cat2 / cat3

In [12]:
# Get category

def get_category_list(s):
    desc_list = clean_desc(s)
    cat = desc_list[1]
    cat = re.sub('.*?: ', '', cat)
    cat = cat[:-1]
    cat = cat.split("-")

    cat = list(map(lower_case, cat))
    cat = list(map(no_accent_vietnamese, cat))
    cat = list(map(remove_special_character, cat))

    # Remove shopee
    cat = cat[1:]
    
    return cat

def first_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 1:
        cat = cat_list[0]
        # cat = lower_case(cat)
        # cat = no_accent_vietnamese(cat)
        
    else:
        cat = ""
    
    return cat


def second_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 2:
        cat = cat_list[0] + " / " + cat_list[1]
        # cat = lower_case(cat)
        # cat = no_accent_vietnamese(cat)
    else:
        cat = ""
    
    return cat

def third_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 3:
        cat = cat_list[0] + " / " + cat_list[1] + " / " + cat_list[2]
        # cat = lower_case(cat)
        # cat = no_accent_vietnamese(cat)
    else:
        cat = ""
    
    return cat

udf_first_cat = udf(first_cat)
udf_second_cat = udf(second_cat)
udf_third_cat = udf(third_cat)


**Product's review**
- 3,2k -> 3200

In [13]:
# 3,2k -> 3200

def k_to_number(s):

    s = str(s)
    
    if "," in s:
        s = re.sub(',', '', s)
        s = re.sub('k', '00', s)
    else:
        s = re.sub('k', '000', s)
    
    return s

udf_clean_num_review = udf(k_to_number)

# df.withColumn("num_review", udf_clean_num_review(df["num_review"])).select("num_review").show(10, truncate=False)

**Shop info**

In [14]:
def get_shop_info_list(s):
    list = s.split("\n")
    
    return list

# udf_get_shop_info_list = udf(get_shop_info_list)
# df.withColumn("new_info", udf_clean_num_review(df["shop_info"])).select("new_info").show(100, truncate=False)

**Liked tier (Yeu thich, Yeu thich+)**

In [15]:
# Get liked shop

def liked_shop(s):
    info_list = s.split("\n")

    if info_list[0] == "Yêu Thích+":
        tier = 2
    elif info_list[0] == "Yêu Thích":
        tier = 1
    else:
        tier = 0
    return tier

udf_liked_shop= udf(liked_shop)
# df.withColumn("shop_liked_tier", udf_liked_shop(df["shop_info"])).select("shop_liked_tier").show(10, truncate=False)

**Shop's reviews**

In [16]:
# Get amount of shop's reviews

def get_shop_num_review(s):
    info_list = s.split("\n")
    
    index = info_list.index('Đánh Giá')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_review = udf(get_shop_num_review)
# df.withColumn("shop_num_review", udf_get_shop_num_review(df["shop_info"])).select("shop_num_review").show(10, truncate=False)

**Shop's product**

In [17]:
# Get amount of shop product

def get_shop_num_product(s):
    info_list = s.split("\n")
    
    index = info_list.index('Sản Phẩm')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_product= udf(get_shop_num_product)
# df.withColumn("shop_num_product", udf_get_shop_num_product(df["shop_info"])).select("shop_num_product").show(100, truncate=False)

**Shop's reply percentages**

In [18]:
# Get reply percentages

def get_reply_percentage(s):
    info_list = s.split("\n")
    
    index = info_list.index('Tỉ Lệ Phản Hồi')
    value = info_list[index+1]
    value = float(value.strip('%'))/100
    
    return value

udf_get_reply_percentage= udf(get_reply_percentage)
# df.withColumn("reply_percentage", udf_get_reply_percentage(df["shop_info"])).select("reply_percentage").show(100, truncate=False)

**Shop's reply time**

In [19]:
# Get reply time

def get_reply_time(s):
    info_list = s.split("\n")
    
    index = info_list.index('Thời Gian Phản Hồi')
    value = info_list[index+1]
    
    value = lower_case(value)
    value = no_accent_vietnamese(value)   
    value = remove_special_character(value)

    return value

udf_get_reply_time= udf(get_reply_time)
# df.withColumn("reply_time", udf_get_reply_time(df["shop_info"])).select("reply_time").show(100, truncate=False)

**Shop's creation time**

In [20]:
# Get shop creation time
def normalize_date(s):

    # Get the number
    num = s.split(" ")[0]

    if "năm" in s:
        num = str(int(num)*12)
    elif "tháng" in s:
        num = num
    else:
        num = 0
    return num

def get_shop_creation_time(s):
    info_list = s.split("\n")
    
    index = info_list.index('Tham Gia')
    value = info_list[index+1]
    value = normalize_date(value)

    return value

udf_get_shop_creation_time= udf(get_shop_creation_time)
# df.withColumn("shop_creation_time", udf_get_shop_creation_time(df["shop_info"])).select("shop_creation_time").show(100, truncate=False)

**Shop's follower**

In [21]:
# Get amount of shop follower
def get_shop_num_follower(s):
    info_list = s.split("\n")
    
    index = info_list.index('Người Theo Dõi')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_follower= udf(get_shop_num_follower)
# df.withColumn("shop_num_follower", udf_get_shop_num_follower(df["shop_info"])).select("shop_num_follower").show(100, truncate=False)

**Shipping**

In [22]:
def clean_shipping(s):
    s = str(s)
    s = re.sub('None', '', s)
    s = clean_product_name(s)
    return s

udf_clean_shipping = udf(clean_shipping)

**Attrs**

In [23]:
def clean_atrrs(s):
    s = str(s)
    s = lower_case(s)
    s = no_accent_vietnamese(s)   
    s = remove_special_character(s) 
    s = s[1:-1]
    return s  

udf_clean_atrrs = udf(clean_atrrs)

# Assembles!

**Cleaning**

In [24]:
# df.show(1000, truncate = False)

# cleaned product name
df_cleaned = df.withColumn("product_name", udf_clean_product_name(df["product_name"]))

# Cleaned price
df_cleaned = df_cleaned.withColumn("price", udf_clean_price(df["price"]))

# Get country, brand, stocks, origin
df_cleaned = df_cleaned.withColumn("country", udf_get_country(df["product_desc"]))
df_cleaned = df_cleaned.withColumn("brand", udf_get_brand(df["product_desc"]))
df_cleaned = df_cleaned.withColumn("stock", udf_get_stock(df["product_desc"]))
df_cleaned = df_cleaned.withColumn("origin", udf_get_origin(df["product_desc"]))

# Get category
df_cleaned = df_cleaned.withColumn("first_category", udf_first_cat(df["product_desc"]))
df_cleaned = df_cleaned.withColumn("second_category", udf_second_cat(df["product_desc"]))
df_cleaned = df_cleaned.withColumn("third_category", udf_third_cat(df["product_desc"]))

# Desc
df_cleaned = df_cleaned.withColumn("description", udf_get_smaller_desc_list(df["product_desc"]))

# Attrs
df_cleaned = df_cleaned.withColumn("attrs", udf_clean_atrrs(df["attrs"]))

# Shop info
if "shop_info" in df_cleaned.columns:
    df_cleaned = df_cleaned.withColumn("shop_like_tier", udf_liked_shop(df["shop_info"]))
    df_cleaned = df_cleaned.withColumn("shop_num_review", udf_get_shop_num_review(df["shop_info"]))
    df_cleaned = df_cleaned.withColumn("shop_reply_percentage", udf_get_reply_percentage(df["shop_info"]))
    df_cleaned = df_cleaned.withColumn("shop_reply_time", udf_get_reply_time(df["shop_info"]))
    df_cleaned = df_cleaned.withColumn("shop_creation_time", udf_get_shop_creation_time(df["shop_info"]))
    df_cleaned = df_cleaned.withColumn("shop_num_follower", udf_get_shop_num_follower(df["shop_info"]))

    # Shipping
    df_cleaned = df_cleaned.withColumn("shipping", udf_clean_shipping(df["shipping"]))

# Number of product review
df_cleaned = df_cleaned.withColumn("num_review", udf_clean_num_review(df["num_review"]))

# Number of product sold
df_cleaned = df_cleaned.withColumn("num_sold", udf_clean_num_review(df["num_sold"]))

# Drop redundant columns
df_cleaned = df_cleaned.drop('product_desc')
df_cleaned = df_cleaned.drop('shop_info')


# df_cleaned.show(100, truncate= False)

**Change data type**

In [25]:
df_cleaned = df_cleaned.withColumn("price",df_cleaned["price"].cast('int'))
df_cleaned = df_cleaned.withColumn("num_review",df_cleaned["num_review"].cast('int'))
df_cleaned = df_cleaned.withColumn("num_sold",df_cleaned["num_sold"].cast('int'))
df_cleaned = df_cleaned.withColumn("stock",df_cleaned["stock"].cast('int'))
df_cleaned = df_cleaned.withColumn("avg_rating",df_cleaned["avg_rating"].cast('double'))


if "shop_info" in df_cleaned.columns:
    df_cleaned = df_cleaned.withColumn("shop_like_tier",df_cleaned["shop_like_tier"].cast('int'))
    df_cleaned = df_cleaned.withColumn("shop_num_review",df_cleaned["shop_num_review"].cast('int'))
    df_cleaned = df_cleaned.withColumn("shop_num_follower",df_cleaned["shop_num_follower"].cast('int'))
    df_cleaned = df_cleaned.withColumn("shop_creation_time",df_cleaned["shop_creation_time"].cast('int'))
    df_cleaned = df_cleaned.withColumn("shop_reply_percentage",df_cleaned["shop_reply_percentage"].cast('double'))
    
df_cleaned.printSchema()

root
 |-- product_name: string (nullable = true)
 |-- shipping: string (nullable = true)
 |-- price: integer (nullable = true)
 |-- avg_rating: double (nullable = true)
 |-- num_review: integer (nullable = true)
 |-- num_sold: integer (nullable = true)
 |-- attrs: string (nullable = true)
 |-- url: string (nullable = true)
 |-- country: string (nullable = true)
 |-- brand: string (nullable = true)
 |-- stock: integer (nullable = true)
 |-- origin: string (nullable = true)
 |-- first_category: string (nullable = true)
 |-- second_category: string (nullable = true)
 |-- third_category: string (nullable = true)
 |-- description: string (nullable = true)
 |-- shop_like_tier: string (nullable = true)
 |-- shop_num_review: string (nullable = true)
 |-- shop_reply_percentage: string (nullable = true)
 |-- shop_reply_time: string (nullable = true)
 |-- shop_creation_time: string (nullable = true)
 |-- shop_num_follower: string (nullable = true)



In [30]:
# # One last check
# df_cleaned.show(100, truncate=False)

**Group, keep highest price**

In [29]:
from pyspark.sql import Window
from pyspark.sql.functions import col, row_number

# Match product name, get highest price
w = Window.partitionBy('product_name').orderBy(col("price").desc())

df_cleaned = df_cleaned.withColumn("row",row_number().over(w)).filter(col("row") == 1).drop("row")

df_cleaned.show(100, truncate=False)

+----------------------------------------------------------------------------------------------------------------------------------------+---------------------------------------------+------+----------+----------+--------+-------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+---------------------+---------+------+----------------------------+----------------+-----------------------------------------------+----------------------------------------------------------------+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

**Go go CSV**

In [28]:
df_cleaned.write.option("header", True).mode('overwrite').csv("/home/jazzdung/E-Commerce-Support-System/mr_clean/clean_af.csv")